In [1]:
import duckdb
import geopandas as gpd


* [Geography from French towns](https://www.data.gouv.fr/datasets/communes-france-1)

In [7]:
all_towns = "./data_sources/communes-france.geojson"
all_towns_target = "./data_target/communes-france.parquet"

In [3]:
con = duckdb.connect()
con.execute("INSTALL spatial; LOAD spatial;")

In [ ]:
con.execute(f"""
    COPY (
        SELECT
            com_code[1]::CHAR(5) AS id,
            com_current_code[1]::CHAR(5) as curren_code,
            com_name [1]::VARCHAR(255) AS name,
            com_name_upper AS name_upper,
            com_name_lower AS name_lower,
            com_siren_code AS siren_code,
            arrdep_name[1]::VARCHAR(255) AS arrondissement_name,
            arrdep_code[1]::CHAR(7) AS arrondissement_code,
            dep_name[1]::VARCHAR(255) AS department_name,
            dep_code[1]::CHAR(3) AS department_code,
            reg_name[1]::VARCHAR(255) AS region_name,
            reg_code[1]::INTEGER AS region_code,
            geom AS geometry,
            geo_point_2d,
            ST_Area(ST_Transform(geom, 'EPSG:4326', 'EPSG:2154')) as area_m2,
            ST_Centroid(geom) as centroid,
            ST_XMin(geom) as bbox_xmin,
            ST_XMax(geom) as bbox_xmax,
            ST_YMin(geom) as bbox_ymin,
            ST_YMax(geom) as bbox_ymax,
            ST_Perimeter(geom) as perimeter,
            ST_NumInteriorRings(geom) as number_enclaves
        FROM ST_Read('{all_towns}')
    ) TO '{all_towns_target}'
    (FORMAT PARQUET)
""")

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [34]:
result_min = con.execute(f"""
    SELECT *
    FROM read_parquet('{all_towns_target}')
    ORDER BY area_m2 ASC
    LIMIT 1
""").fetchdf()

# --(SELECT CAST(COUNT(*) * 0.05 AS INTEGER) FROM read_parquet('communes-france.parquet'))

In [35]:
result_min

id curren_code                  name            name_upper  \
0  33103       33103  Castelmoron-d'Albret  CASTELMORON-D'ALBRET   

             name_lower siren_code arrondissement_name arrondissement_code  \
0  castelmoron-d'albret  213301039              Langon                 333   

  department_name department_code  ... region_code  \
0         Gironde              33  ...          75   

                                            geometry  \
0  [2, 4, 0, 0, 0, 0, 0, 0, 34, 9, 82, 188, 160, ...   

                                        geo_point_2d       area_m2  \
0  { "lon": -0.011633028929666523, "lat": 44.6795...  70750.931927   

                                            centroid bbox_xmin  bbox_xmax  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, ...  -0.01282  -0.010103   

   bbox_ymin  bbox_ymax  number_enclaves  
0  44.678348  44.680982                0  

[1 rows x 21 columns]

In [36]:
enclaves = con.execute(f"""
    SELECT *
    FROM read_parquet('{all_towns_target}')
    WHERE number_enclaves > 0
""").fetchdf()

In [37]:
enclaves

id curren_code                          name  \
0   51176       51176                        Corroy   
1   52140       52140     Colombey les Deux Églises   
2   60535       60535              Reuil-sur-Brêche   
3   67486       67486                     Sundhouse   
4   82189       82189                       Vazerac   
5   62269       62269                        Diéval   
6   09042       09042           La Bastide-de-Sérou   
7   02232       02232                      Coyolles   
8   61069       61069                         Cahan   
9   49228       49228               Noyant-Villages   
10  14174       14174            Condé-en-Normandie   
11  32266       32266             Moncorneil-Grazan   
12  68078       68078                     Eguisheim   
13  05052       05052                      Eygliers   
14  53066       53066                       Chemazé   
15  08173       08173                         Flize   
16  67108       67108                    Duppigheim   
17  61474       61474              Gouffern en Auge   
18  48080       48080                      Langogne   
19  71028       71028                   Beauvernois   
20  56046       56046                         Crach   
21  88415       88415  Saint-Étienne-lès-Remiremont   

                      name_upper                    name_lower siren_code  \
0                         CORROY                        corroy  215101650   
1      COLOMBEY LES DEUX ÉGLISES     colombey les deux églises  200069334   
2               REUIL-SUR-BRÊCHE              reuil-sur-brêche  216005298   
3                      SUNDHOUSE                     sundhouse  216704866   
4                        VAZERAC                       vazerac  218201895   
5                         DIÉVAL                        diéval  216202697   
6            LA BASTIDE-DE-SÉROU           la bastide-de-sérou  210900429   
7                       COYOLLES                      coyolles  210202172   
8                          CAHAN                         cahan  216100693   
9                NOYANT-VILLAGES               noyant-villages  200070050   
10            CONDÉ-EN-NORMANDIE            condé-en-normandie  200056877   
11             MONCORNEIL-GRAZAN             moncorneil-grazan  213202666   
12                     EGUISHEIM                     eguisheim  216800789   
13                      EYGLIERS                      eygliers  210500526   
14                       CHEMAZÉ                       chemazé  215300666   
15                         FLIZE                         flize  200085983   
16                    DUPPIGHEIM                    duppigheim  216701086   
17              GOUFFERN EN AUGE              gouffern en auge  200066256   
18                      LANGOGNE                      langogne  214800807   
19                   BEAUVERNOIS                   beauvernois  217100288   
20                         CRACH                         crach  215600461   
21  SAINT-ÉTIENNE-LÈS-REMIREMONT  saint-étienne-lès-remiremont  218804151   

     arrondissement_name arrondissement_code  department_name department_code  \
0                Épernay                 512            Marne              51   
1               Chaumont                 521      Haute-Marne              52   
2               Clermont                 602             Oise              60   
3       Sélestat-Erstein                 675         Bas-Rhin              67   
4              Montauban                 822  Tarn-et-Garonne              82   
5                Béthune                 622    Pas-de-Calais              62   
6           Saint-Girons                 093           Ariège              09   
7               Soissons                 024            Aisne              02   
8               Argentan                 612             Orne              61   
9                 Saumur                 493   Maine-et-Loire              49   
10                  Vire                 144         Calvados              14 

In [28]:
result_max = con.execute(f"""
    SELECT *
    FROM read_parquet('{all_towns_target}')
    ORDER BY area_m2 DESC
    LIMIT 50
""").fetchdf()


In [29]:
result_max

reg_code_test                                       geo_point_2d  year  \
0             989  { "lon": -109.22126424250821, "lat": 10.297389...  2025   
1             986  { "lon": -178.15526303546318, "lat": -14.27041...  2025   
2             986  { "lon": -176.16192791819358, "lat": -13.28186...  2025   
3             986  { "lon": -178.06416451720403, "lat": -14.32593...  2025   
4             984  { "lon": 138.99284362792966, "lat": -59.995894...  2025   
5               3  { "lon": -53.758237342936297, "lat": 2.9674285...  2025   
6               3  { "lon": -52.531259042136021, "lat": 3.9255912...  2025   
7               3  { "lon": -52.79651667614467, "lat": 2.83806589...  2025   
8               3  { "lon": -53.64545785664356, "lat": 4.98975165...  2025   
9               3  { "lon": -53.100581385144146, "lat": 4.5292891...  2025   
10              3  { "lon": -53.978027718853923, "lat": 4.9478083...  2025   
11              3  { "lon": -53.39848043867601, "lat": 3.91380229...  2025   
12              3  { "lon": -52.515333449551321, "lat": 4.4613292...  2025   
13              3  { "lon": -54.035086238696834, "lat": 4.0429681...  2025   
14              3  { "lon": -52.132609399443425, "lat": 3.7418256...  2025   
15              3  { "lon": -53.322956465481873, "lat": 5.2575092...  2025   
16              3  { "lon": -54.269342938734944, "lat": 4.8302565...  2025   
17              3  { "lon": -54.186330375841145, "lat": 4.3892460...  2025   
18              3  { "lon": -52.766834835406684, "lat": 4.9322904...  2025   
19              3  { "lon": -53.010542383014482, "lat": 5.2111348...  2025   
20              3  { "lon": -51.810249749205035, "lat": 4.1903626...  2025   
21              3  { "lon": -52.509812305664624, "lat": 4.8095340...  2025   
22            975  { "lon": -56.324419805970791, "lat": 46.951611...  2025   
23            984  { "lon": 69.488949534211045, "lat": -49.296080...  2025   
24              3  { "lon": -52.509557614304654, "lat": 4.9772795...  2025   
25              1  { "lon": -61.657503215992691, "lat": 16.171660...  2025   
26              1  { "lon": -61.710629105643264, "lat": 16.293741...  2025   
27              3  { "lon": -53.916865135481956, "lat": 5.6855372...  2025   
28              1  { "lon": -61.611692367687517, "lat": 16.055217...  2025   
29              1  { "lon": -61.371356348472879, "lat": 16.320279...  2025   
30              1  { "lon": -61.387454751281993, "lat": 16.257423...  2025   
31            978  { "lon": -63.055070631098111, "lat": 18.077620...  2025   
32              1  { "lon": -61.449888021245101, "lat": 16.389651...  2025   
33              3  { "lon": -52.34388725068321, "lat": 4.83027249...  2025   
34              1  { "lon": -61.5018187985876, "lat": 16.27280243...  2025   
35              1  { "lon": -61.471813474521333, "lat": 16.324584...  2025   
36              1  { "lon": -61.668623130081158, "lat": 16.241389...  2025   
37              1  { "lon": -61.462005869976224, "lat": 16.465342...  2025   
38              1  { "lon": -61.763539328883134, "lat": 16.227356...  2025   
39              1  { "lon": -61.726189760825527, "lat": 16.086823...  2025   
40              1  { "lon": -61.613882283103059, "lat": 16.121636...  2025   
41              1  { "lon": -61.281138772452849, "lat": 16.272959...  2025   
42              2  { "lon": -60.991850884113177, "lat": 14.627696...  2025   
43             93  { "lon": 4.6616709664294165, "lat": 43.5470638...  2025   
44              1  { "lon": -61.275603716250707, "lat": 15.966193...  2025   
45              1  { "lon": -61.293934890617763, "lat": 15.906098...  2025   
46              2  { "lon": -60.905208542457771, "lat": 14.606419...  2025   
47              2  { "lon": -61.076526410608693, "lat": 14.801268...  2025   
48              1  { "lon": -61.592036343265029, "lat": 16.251653...  2025   
49              1  { "lon": -61.469597106151234, "lat": 16.225232...  2025   

   reg_code              

In [ ]:
gdf = gpd.read_parquet("communes-france.parquet")

# Filter in pandas/geopandas instead
gdf = gdf.nsmallest(1, "area_m2")

gdf

In [ ]:
gdf.plot()